In [9]:
# @author: Núria Queralt Rosinach
# @date: 01-15-2018
# @version: v2

## Prepare Monarch edges to build the graph
* build statements file
* build concepts file

In [1]:
import os, sys
import pandas as pd
import datetime
sys.path.insert(0, '/home/nuria/soft/utils3/lib')
import abravo_lib as utils

In [2]:
# timestamp
today = datetime.date.today()

# path to data
path = os.getcwd() + '/add-connections-to-net'
if not os.path.isdir(path): os.makedirs(path)
    
# read data
sys.path.insert(0, './add-connections-to-net/')

## Input: Monarch statements

In [3]:
# open new_connections file
edges_df = pd.read_table('./get-monarch-connections/monarch_connections.tsv')
edges_df.head(2)

subject_id subject_label    relation_id  \
0         RGD:2145          Aqp7     RO:0002434   
1  NCBIGene:427417         CREB3  RO:HOM0000020   

                          relation_label    object_id object_label  \
0                         interacts with  RGD:1303263          Gk2   
1  in 1 to 1 orthology relationship with    MGI:99946        Creb3   

  reference_id_list  
0               NaN  
1               NaN

## Generate statement file

##### NEO4J file features
- Include 'NA'
- one row= one association with all references collapsed in a string as a list
- References as URIs:
    - multi-term pubmed url; pipelined from other urls
    - PubMed: base_uri/{pmid,pmid,pmid,no_pmid}; base_uri: pubmed.nih.gov/
    - Others: expand context to the correct url for not pmids, e.g. react:, ... (first as a list of id)

In [8]:
# add attribute/columns: 'rel_term_id', 'rel_term_label', rel_term_iri to file
# authoritative url
uriPrefixes_dct = {
    'pmid': 'https://www.ncbi.nlm.nih.gov/pubmed/', #'http://identifiers.org/pubmed/', 
    'react': 'http://reactome.org/content/detail/', #'http://identifiers.org/reactome/', 
    'zfin': 'http://zfin.org/',
    'go_ref': 'http://purl.obolibrary.org/obo/go/references/', #'http://identifiers.org/go.ref/GO_REF:', 
    'mgi': 'http://www.informatics.jax.org/accession/MGI:', #'http://identifiers.org/mgi/MGI:'
    'flybase': 'http://flybase.org/reports/',
    'wormbase': 'http://www.wormbase.org/resources/paper/',
    'isbn-10': 'https://www.wikidata.org/wiki/Special:BookSources/',
    'isbn-13': 'https://www.wikidata.org/wiki/Special:BookSources/'
}
# source/database
dbPrefixes_dct = {
    'na': 'NA',
    'mgi': 'http://www.informatics.jax.org/',
    'fb': 'http://flybase.org/',
    'rgd': 'http://rgd.mcw.edu/', 
    'zfin': 'http://zfin.org/',
    'sgd': 'https://www.yeastgenome.org/',
    'xenbase': 'http://www.xenbase.org/'
}
ref_text = 'NA'
ref_date = 'NA' 
with open('./add-connections-to-net/monarch_edges_v{}.tsv'.format(today), 'w') as f:
    f.write(
        'subject_id\tproperty_id\tobject_id\treference_uri\treference_supporting_text\treference_date\tproperty_label\tproperty_description\tproperty_uri\n'
           )
    header = 1
    for row in open('./get-monarch-connections/monarch_connections.tsv').readlines():
        if header:
            header = 0
            continue
        edge = row.strip('\n').split('\t')
        ref_uri_l = list()
        # expand to uri or NA
        pmid_l = list()
        for ref in edge[-1].strip().split('|'):
            # NA or database
            if ':' not in ref:
                ref_uri = dbPrefixes_dct[ref.lower()]
                ref_uri_l.append(ref_uri)
            # publications
            else:
                pref, uriId = ref.split(':')
                # separate pmid from non pmid
                if ref.startswith('PMID'):
                    pmid_l.append(uriId)
                else:
                    ref_uri = uriPrefixes_dct[pref.lower()] + uriId
                    ref_uri_l.append(ref_uri)
        # create multi-term pubmed url
        if len(pmid_l):
            pmid_s = ','.join(pmid_l)
            ref_uri = uriPrefixes_dct['pmid'] + pmid_s
            ref_uri_l.append(ref_uri)
        ref_uri_list = '|'.join(ref_uri_l)
        # write the associations + list of references as uri or NA
        sub_id = 'NA' if edge[0] is None else edge[0]
        rel_id = 'NA' if edge[2] is None else edge[2] 
        obj_id = 'NA' if edge[4] is None else edge[4]
        rel_label = 'NA' if edge[3] is None else edge[3]
        rel_def = 'NA' #if edge[5] is None else edge[5] 
        if ':' in rel_id:
            rel_iri = 'http://purl.obolibrary.org/obo/' + rel_id.replace(':', '_')
        else:
            rel_iri = rel_id
        f.write('{}\t{}\t{}\t{}\t{}\t{}\t{}\t{}\t{}\n'.format(sub_id, rel_id, obj_id, ref_uri_list, ref_text, ref_date, rel_label, rel_def, rel_iri))
        print(sub_id, rel_id, obj_id, ref_uri_list, ref_text, ref_date, rel_label, rel_def, rel_iri)        

RGD:2145 RO:0002434 RGD:1303263 NA NA NA interacts with NA http://purl.obolibrary.org/obo/RO_0002434
NCBIGene:427417 RO:HOM0000020 MGI:99946 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
FlyBase:FBgn0037244 RO:0002206 CL:0000023 NA NA NA expressed in NA http://purl.obolibrary.org/obo/RO_0002206
Xenbase:XB-GENE-990196 RO:HOM0000020 MGI:88263 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
MGI:1309991 RO:HOM0000017 RGD:1359411 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:87883 RO:0002200 MP:0001541 https://www.ncbi.nlm.nih.gov/pubmed/8898228 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
KEGG-path:maphsa04976 None HP:0004305 https://www.ncbi.nlm.nih.gov/pubmed/8208891,21212106,2700694,6138131,19498335 NA NA None NA None
MGI:5011587 RO:HOM0000017 RGD:1583076 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo

SGD:S000002296 RO:0002200 MONARCH:APO_0000109APO_0000003 https://www.ncbi.nlm.nih.gov/pubmed/9748261 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
NCBIGene:106505015 RO:HOM0000017 ZFIN:ZDB-GENE-040630-5 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
:.well-known/genid/genoGM26585 None HP:0200136 https://www.ncbi.nlm.nih.gov/pubmed/25220016 NA NA None NA None
Xenbase:XB-GENE-5797733 RO:HOM0000017 NCBIGene:796215 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:894679 RO:HOM0000020 NCBIGene:100616516 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
SGD:S000003966 RO:HOM0000017 WormBase:WBGene00000176 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
REACT:R-HSA-382551 None HP:0000099 https://www.ncbi.nlm.nih.gov/pubmed/3429065,25305756,14714961,17474561,813757,3789948,6117979,21323541,12945726,25646370,4

NCBIGene:100145893 RO:HOM0000017 FlyBase:FBgn0034884 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:96911 RO:HOM0000011 MGI:99951 NA NA NA in paralogy relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000011
HGNC:3219 RO:0002200 HP:0000776 https://www.ncbi.nlm.nih.gov/pubmed/8985490,16685658,20389311,19664000,15776121,17937443,23532871,22943132 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
FlyBase:FBgn0003371 RO:0002200 FBbt:00000406PHENOTYPE https://www.ncbi.nlm.nih.gov/pubmed/2570722 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
NCBIGene:820142 RO:HOM0000017 FlyBase:FBgn0261014 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
NCBIGene:821720 RO:HOM0000017 HGNC:15912 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:103201 RO:0002331 GO:0051458 https://www.ncbi.nlm.nih.gov/pubmed/18511498 NA NA involved in NA http:

ZFIN:ZDB-GENE-120525-2 RO:HOM0000017 HGNC:14078 http://zfin.org/ZDB-PUB-030905-1|https://www.ncbi.nlm.nih.gov/pubmed/26992035,25982796 NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:1289301 RO:HOM0000020 FlyBase:FBgn0035830 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
NCBIGene:702836 RO:HOM0000020 HGNC:640 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
MGI:99951 RO:0002434 MGI:108420 https://www.ncbi.nlm.nih.gov/pubmed/20211142,18358244 NA NA interacts with NA http://purl.obolibrary.org/obo/RO_0002434
NCBIGene:100024281 RO:HOM0000017 RGD:1305167 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
ZFIN:ZDB-GENE-060810-84 RO:HOM0000020 MGI:107687 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
NCBIGene:100552250 RO:HOM0000020 RGD:621587 NA NA NA in 1 to 1 orthology rel

SGD:S000000763 RO:0002200 MONARCH:APO_0000215APO_0000004 https://www.ncbi.nlm.nih.gov/pubmed/16361226 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
RGD:1303263 RO:HOM0000017 NCBIGene:100051712 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
NCBIGene:100126859 RO:HOM0000017 FlyBase:FBgn0010397 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
HGNC:19297 RO:0002206 UBERON:0001162 NA NA NA expressed in NA http://purl.obolibrary.org/obo/RO_0002206
MGI:96794 RO:HOM0000017 WormBase:WBGene00002054 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:108064 RO:0002327 GO:0042802 http://purl.obolibrary.org/obo/go/references/0000096|http://www.informatics.jax.org/accession/MGI:4834177 NA NA enables NA http://purl.obolibrary.org/obo/RO_0002327
NCBIGene:100616510 RO:HOM0000017 ZFIN:ZDB-GENE-090312-2 NA NA NA in orthology relationship with NA http://purl.obolibrary

...

HGNC:634 RO:HOM0000020 NCBIGene:539870 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
MGI:103036 RO:0002200 MP:0002169 https://www.ncbi.nlm.nih.gov/pubmed/22520852 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
ZFIN:ZDB-GENE-030912-10 RO:HOM0000017 Xenbase:XB-GENE-6076923 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
HGNC:12613 RO:0002434 HGNC:12468 https://www.ncbi.nlm.nih.gov/pubmed/20622874,19373254,28190767,28088760,24850914,16005295,22626734,25527291 NA NA interacts with NA http://purl.obolibrary.org/obo/RO_0002434
MGI:1857807 RO:0002200 MP:0006423 https://www.ncbi.nlm.nih.gov/pubmed/11698654 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
WormBase:WBGene00013924 RO:HOM0000017 NCBIGene:825875 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
NCBIGene:837150 RO:HOM0000017 FlyBase:FBgn0003371 NA NA NA in orthology relation

RGD:1308668 RO:HOM0000020 HGNC:21205 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
NCBIGene:100029625 RO:HOM0000020 HGNC:3236 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
HGNC:14078 RO:0002206 CL:0002328 NA NA NA expressed in NA http://purl.obolibrary.org/obo/RO_0002206
HGNC:23177 RO:0002331 REACT:R-HSA-392499 NA NA NA involved in NA http://purl.obolibrary.org/obo/RO_0002331
WormBase:WBGene00013111 RO:HOM0000017 NCBIGene:100052904 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
REACT:R-HSA-1430728 None HP:0002093 https://www.ncbi.nlm.nih.gov/pubmed/22664479,1980322,16078127,27182965,22055160,18265924,28166215,22411247,29273806,15702148,26767831,7553819,19451621,12677708,17334013,28167095,12393443,16617686,7516075,2109631,17845577,21844665,14526151,20864067,23228682,1359816,12395734,21685187,12534036,19483681,9009997,22885965,7668832,519945,9273467,2

NCBIGene:100059300 RO:HOM0000020 ZFIN:ZDB-GENE-050320-147 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
MGI:1891209 RO:0002200 MP:0011098 NA NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
SGD:S000005471 RO:0002200 MONARCH:APO_0000149APO_0000004 https://www.ncbi.nlm.nih.gov/pubmed/23045389 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
NCBIGene:695404 RO:HOM0000020 ZFIN:ZDB-GENE-120319-2 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
KEGG-path:maphsa04141 None HP:0002650 https://www.ncbi.nlm.nih.gov/pubmed/25220016 NA NA None NA None
SGD:S000000154 RO:0002200 MONARCH:APO_0000041APO_0000005 https://www.ncbi.nlm.nih.gov/pubmed/22384326 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
REACT:R-HSA-597592 None HP:0000520 https://www.ncbi.nlm.nih.gov/pubmed/25027321,21178798,1079072,19682621,2086476,6238056,3808623,19541266,3022220,621838,1800178

FlyBase:FBgn0015282 RO:0002200 GO:0044754PHENOTYPE https://www.ncbi.nlm.nih.gov/pubmed/27559127 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
WormBase:WBGene00001345 RO:HOM0000017 FlyBase:FBgn0028550 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
ZFIN:ZDB-GENE-051113-160 RO:HOM0000017 NCBIGene:831466 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
MGI:99946 RO:HOM0000017 WormBase:WBGene00002783 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
NCBIGene:100627848 RO:HOM0000020 HGNC:11306 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
MGI:1345634 RO:0002434 MGI:98889 https://www.ncbi.nlm.nih.gov/pubmed/28190767 NA NA interacts with NA http://purl.obolibrary.org/obo/RO_0002434
HGNC:6636 RO:0002200 HP:0001513 https://www.ncbi.nlm.nih.gov/pubmed/12596689,23552003,11410834,19741171,19720629 NA NA has phenotyp

HGNC:660 RO:HOM0000017 SGD:S000002296 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
WormBase:WBGene00007352 RO:0002434 WormBase:WBGene00013924 NA NA NA interacts with NA http://purl.obolibrary.org/obo/RO_0002434
NCBIGene:100517203 RO:HOM0000020 ZFIN:ZDB-GENE-001221-1 NA NA NA in 1 to 1 orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000020
NCBIGene:712901 RO:HOM0000017 FlyBase:FBgn0034884 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
WormBase:WBGene00017814 RO:HOM0000017 NCBIGene:395309 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
NCBIGene:100023076 RO:HOM0000017 FlyBase:FBgn0039235 NA NA NA in orthology relationship with NA http://purl.obolibrary.org/obo/RO_HOM0000017
ClinVarVariant:221577 RO:0002200 HP:0000970 https://www.ncbi.nlm.nih.gov/pubmed/25220016,27388694 NA NA has phenotype NA http://purl.obolibrary.org/obo/RO_0002200
MGI:98889 R

## Generate concept file

In [9]:
# semantic groups dictionary
# collide concepts
concept_dct = dict()
header = 1
for row in open('./get-monarch-connections/monarch_connections.tsv').readlines():
    if header:
        header = 0
        continue
    fields = row.strip('\n').split('\t')
    sid = fields[0]
    oid = fields[4]
    concept_dct[sid] = {}
    concept_dct[oid] = {}
print(len(concept_dct.keys()))

# list of concept prefixes
conceptPrefix_dct = dict()
for concept in concept_dct:
    conceptPrefix_dct[concept.split(':')[0]] = 1
print(conceptPrefix_dct.keys())
    
# build conceptPrefix2semantic dict
conceptPrefix2semantic_dct = dict()
for prefix in conceptPrefix_dct:
    prefix = prefix.lower()
    if 'variant' in prefix:
        conceptPrefix2semantic_dct[prefix] = 'VARI'
    elif 'phenotype' in prefix or 'mondo' in prefix or 'omim' in prefix or 'doid' in prefix or 'mesh' in prefix or 'hp' in prefix or 'mp' in prefix or 'fbcv' in prefix or 'fbbt' in prefix or 'zp' in prefix or 'apo' in prefix or 'trait' in prefix:
        conceptPrefix2semantic_dct[prefix] = 'DISO'
    elif 'gene' in prefix or 'hgnc' in prefix or 'ensembl' in prefix or 'mgi' in prefix or 'flybase' in prefix or 'wormbase' in prefix or 'xenbase' in prefix or 'zfin' in prefix or 'rgd' in prefix or 'sgd' in prefix:
        conceptPrefix2semantic_dct[prefix] = 'GENE'
    elif 'react' in prefix or 'kegg-path' in prefix or 'go' in prefix:
        conceptPrefix2semantic_dct[prefix] = 'PHYS'
    elif 'uberon' in prefix or 'cl' in prefix:
        conceptPrefix2semantic_dct[prefix] = 'ANAT'
    elif 'coriell' in prefix or 'monarch' in prefix or 'mmrrc' in prefix or '' in prefix:
        conceptPrefix2semantic_dct[prefix] = 'GENO'
    else:
        conceptPrefix2semantic_dct[prefix] = 'CONC'

4644
dict_keys(['RGD', 'NCBIGene', 'MGI', 'FlyBase', 'CL', 'Xenbase', 'MP', 'KEGG-path', 'HP', 'HGNC', 'GO', 'FBcv', 'ZFIN', 'WormBase', 'WBPhenotype', 'SGD', 'MONARCH', '', 'UBERON', 'ZP', 'REACT', 'FBbt', 'ENSEMBL', 'ClinVarVariant', 'APO', 'Coriell', 'OMIM', 'MONDO', 'AQTLTrait', 'MMRRC'])


In [10]:
# concept attribute dictionaries: id integration of sub and obj IDs in a common data structure
concept_dct = dict()
header = 1
for row in open('./get-monarch-connections/monarch_connections.tsv').readlines():
    if header:
        header = 0
        continue
    fields = row.strip('\n').split('\t')
    # id: integration of sub and obj IDs in a unique data structure
    sid = fields[0]
    slab = fields[1]
    oid = fields[4]
    olab = fields[5]
    # build the concept data structure
    concept_dct[sid] = { 'preflabel': slab, 'semantic_groups': conceptPrefix2semantic_dct.get(sid.split(':')[0].lower(), 'CONC'), 'synonyms': 'NA', 'definition': 'NA' }
    concept_dct[oid] = { 'preflabel': olab, 'semantic_groups': conceptPrefix2semantic_dct.get(oid.split(':')[0].lower(), 'CONC'),'synonyms': 'NA', 'definition': 'NA' }

# check
header = 1
for row in open('./get-monarch-connections/monarch_connections.tsv').readlines():
    if header:
        header = 0
        continue
    fields = row.strip('\n').split('\t')
    sid = fields[0]
    slab = fields[1]
    oid = fields[4]
    olab = fields[5]
    print(sid,slab,concept_dct.get(fields[0]).get('semantic_groups'))
    print(oid,olab,concept_dct.get(fields[4]).get('semantic_groups'))

RGD:2145 Aqp7 GENE
RGD:1303263 Gk2 GENE
NCBIGene:427417 CREB3 GENE
MGI:99946 Creb3 GENE
FlyBase:FBgn0037244 CG14647 GENE
CL:0000023 oocyte ANAT
Xenbase:XB-GENE-990196 capn1 GENE
MGI:88263 Capn1 GENE
MGI:1309991 Krt33b GENE
RGD:1359411 Krt31 GENE
MGI:87883 Acp5 GENE
MP:0001541 abnormal osteoclast physiology DISO
KEGG-path:maphsa04976 Bile secretion PHYS
HP:0004305 Involuntary movements DISO
MGI:5011587 Gm19402 GENE
RGD:1583076 LOC687631 GENE
RGD:3090 Mip GENE
RGD:628763 Aqp11 GENE
RGD:1309121 Fbxw11 GENE
RGD:70982 Gsk3b GENE
HGNC:14078 BACH2 GENE
GO:0000980 RNA polymerase II distal enhancer sequence-specific DNA binding PHYS
FlyBase:FBgn0037788 CG3940 GENE
FBcv:0000709 cell number defective DISO
ZFIN:ZDB-GENE-060526-131 rusc2 GENE
WormBase:WBGene00006753 unc-14 GENE
NCBIGene:100055579 CA9 GENE
FlyBase:FBgn0034554 CG15227 GENE
HGNC:28454 DERL1 GENE
GO:0005783 endoplasmic reticulum PHYS
HGNC:19297 TNK2 GENE
HGNC:19297 TNK2 GENE
FlyBase:FBgn0039147 CG10694 GENE
NCBIGene:431623 RAD23B GENE


WormBase:WBGene00016539 madd-2 GENE
NCBIGene:100157515 MID2 GENE
HGNC:20595 MTUS2 GENE
ZFIN:ZDB-GENE-060130-237 mtus2b GENE
FlyBase:FBgn0261647 Axud1 GENE
HGNC:14300 CSRNP1 GENE
ZFIN:ZDB-GENE-030124-1 nfe2 GENE
ZP:0004542 abnormal(ly) mislocalised otolith DISO
SGD:S000002351 ARF1 GENE
MONARCH:APO_0000144APO_0000003 telomere length:decreased GENO
MGI:96794 Lmna GENE
HP:0000240 Abnormality of skull size DISO
NCBIGene:100623722 GNS GENE
HGNC:4422 GNS GENE
HGNC:12031 TRAF1 GENE
GO:0005515 protein binding PHYS
ZFIN:ZDB-GENE-080218-15 zgc:173570 GENE
ZFIN:ZDB-GENE-061009-29 si:dkey-147f3.4 GENE
WormBase:WBGene00002783 let-607 GENE
Xenbase:XB-GENE-959045 creb3 GENE
NCBIGene:711719 AQP2 GENE
RGD:2142 Aqp2 GENE
NCBIGene:100018582 LOC100018582 GENE
SGD:S000001024 GUT1 GENE
HGNC:25818 BRD9 GENE
UBERON:0002358 peritoneum ANAT
KEGG-path:maphsa04924 Renin secretion PHYS
HP:0000099 Glomerulonephritis DISO
ZFIN:ZDB-GENE-061110-88 ubc GENE
ZFIN:ZDB-GENE-030131-8486 si:ch211-202a12.4 GENE
NCBIGene:39551

MP:0002999 abnormal bone healing DISO
HGNC:27035 UBXN2B GENE
NCBIGene:100029862 UBXN2B GENE
WormBase:WBGene00009958 madd-4 GENE
WormBase:WBGene00020567 T19D2.1 GENE
HGNC:6096 AQP12B GENE
UBERON:0000467 anatomical system ANAT
MGI:99421 Nfe2l1 GENE
HP:0002605 Hepatic necrosis DISO
FlyBase:FBgn0260450 CalpC GENE
NCBIGene:397027 CAPN1 GENE
RGD:1305596 Gykl1 GENE
WormBase:WBGene00020007 R11F4.1 GENE
NCBIGene:827847 ACA6 GENE
RGD:1306426 Car9 GENE
NCBIGene:100126852 GSK3B GENE
FlyBase:FBgn0046332 gskt GENE
RGD:1303263 Gk2 GENE
FlyBase:FBgn0025592 Gk1 GENE
NCBIGene:100126852 GSK3B GENE
WormBase:WBGene00008095 C44H4.6 GENE
SGD:S000000154 SHP1 GENE
MONARCH:APO_0000149APO_0000004 protein/peptide accumulation:increased GENO
ZFIN:ZDB-GENE-051023-7 uba52 GENE
MGI:3648788 Gm5239 GENE
HGNC:7780 NFE2 GENE
GO:0045893 positive regulation of transcription, DNA-templated PHYS
MGI:106594 Gk GENE
UBERON:0000956 cerebral cortex ANAT
NCBIGene:747490 VCP GENE
WormBase:WBGene00008053 cdc-48.2 GENE
HGNC:12032 TR

ZFIN:ZDB-GENE-040426-2793 derl1 GENE
FlyBase:FBgn0267972 Der-1 GENE
MGI:105942 Hcfc1 GENE
MP:0013292 embryonic lethality prior to organogenesis DISO
FlyBase:FBgn0029861 CG3815 GENE
FBbt:00004751PHENOTYPE wing vein phenotype DISO
ZFIN:ZDB-GENE-030131-1515 csrnp1b GENE
ZP:0003176 abnormal(ly) physical object quality midbrain hindbrain boundary DISO
MGI:1341204 Aqp6 GENE
UBERON:0002037 cerebellum ANAT
NCBIGene:100067436 LOC100067436 GENE
MGI:2664636 Aqp12 GENE
HGNC:633 AQP1 GENE
HGNC:23427 KIAA1958 GENE
ZFIN:ZDB-GENE-040426-2793 derl1 GENE
GO:0005783 endoplasmic reticulum PHYS
RGD:1311835 Derl1 GENE
FlyBase:FBgn0267972 Der-1 GENE
REACT:R-HSA-446203 Asparagine N-linked glycosylation PHYS
HP:0100827 Lymphocytosis DISO
HGNC:1144 BTRC GENE
GO:0005515 protein binding PHYS
FlyBase:FBgn0003731 Egfr GENE
FBbt:00000710PHENOTYPE abdominal 2 lateral longitudinal muscle 1 phenotype DISO
ZFIN:ZDB-GENE-041014-85 si:dkey-88n24.5 GENE
NCBIGene:616677 MTUS2 GENE
NCBIGene:100337543 krt36 GENE
MGI:1309993 K

HGNC:6204 JUN GENE
FlyBase:FBgn0033635 Prip GENE
ZFIN:ZDB-GENE-040724-152 aqp4 GENE
FlyBase:FBgn0039235 CG10899 GENE
NCBIGene:827846 ACA4 GENE
NCBIGene:100620522 BACH2 GENE
MGI:894679 Bach2 GENE
:.well-known/genid/mgiseqaltkey2026 tm1Ask GENO
MGI:2174931 Aqp1<tm1Ask>/Aqp1<tm1Ask> [involves: C57BL/6J] GENE
MGI:1919138 Krt33a GENE
UBERON:0001723 tongue ANAT
REACT:R-HSA-382551 Transmembrane transport of small molecules PHYS
HP:0000518 Cataract DISO
FlyBase:FBgn0031947 CG7154 GENE
NCBIGene:835595 AT5G55040 GENE
WormBase:WBGene00020007 R11F4.1 GENE
NCBIGene:538702 LOC538702 GENE
WormBase:WBGene00004346 rgs-3 GENE
NCBIGene:740330 RGS20 GENE
MGI:1858732 Keap1 GENE
MP:0011085 postnatal lethality, complete penetrance DISO
ZFIN:ZDB-GENE-131121-552 fosaa GENE
WormBase:WBGene00021082 zip-11 GENE
FlyBase:FBgn0002525 Lam GENE
FBcv:0000366 female sterile DISO
ClinVarVariant:126424 NM_018297.3(NGLY1):c.1624C>T (p.Arg542Ter) VARI
HP:0008954 Intrinsic hand muscle atrophy DISO
ZFIN:ZDB-GENE-030131-7018 w

...

SGD:S000003733 UBP12 GENE
MONARCH:APO_0000106APO_0000245 vegetative growth:decreased rate GENO
FlyBase:FBgn0259729 CG42383 GENE
MGI:3042273 Nsfl1c GENE
WormBase:WBGene00004502 rpt-2 GENE
Xenbase:XB-GENE-950579 psmc1 GENE
RGD:1308557 Ubxn2b GENE
NCBIGene:825736 PUX4 GENE
RGD:1308686 Ikzf2 GENE
WormBase:WBGene00017814 F26A10.2 GENE
SGD:S000003966 FPS1 GENE
APO:0000097 auxotrophy DISO
:.well-known/genid/mgiseqaltkey862794 tm1b(EUCOMM)Wtsi GENO
MONARCH:bda1cde5e50b41cb Aqp1<tm1b(EUCOMM)Wtsi>/Aqp1<tm1b(EUCOMM)Wtsi> [C57BL/6NTac-MRC Harwell-H-AQP1-C01-TM1B] (male) GENO
SGD:S000005471 MDY2 GENE
ZFIN:ZDB-GENE-040808-59 rad23aa GENE
WormBase:WBGene00022592 klu-2 GENE
RGD:1307024 Ikzf3 GENE
SGD:S000002296 ARF2 GENE
MONARCH:APO_0000087APO_0000004 resistance to chemicals:increased GENO
NCBIGene:722740 FBXO6 GENE
ZFIN:ZDB-GENE-090312-52 si:rp71-1k13.6 GENE
FlyBase:FBgn0051721 Trim9 GENE
NCBIGene:422131 MID2 GENE
HGNC:620 APP GENE
HGNC:23177 KEAP1 GENE
REACT:R-HSA-382551 Transmembrane transport of s

NCBIGene:817367 ACA2 GENE
FlyBase:FBgn0027538 beta4GalNAcTA GENE
NCBIGene:418341 B4GALT4 GENE
FlyBase:FBgn0032197 CG5694 GENE
CL:0000655 secondary oocyte ANAT
FlyBase:FBgn0261014 TER94 GENE
FBcv:0000370 male sterile DISO
HGNC:9812 RAD23A GENE
FlyBase:FBgn0026777 Rad23 GENE
MGI:101836 Traf1 GENE
UBERON:0000922 embryo ANAT
HGNC:4289 GK GENE
HGNC:633 AQP1 GENE
SGD:S000001840 AQY3 GENE
ZFIN:ZDB-GENE-060503-57 aqp10b GENE
ZFIN:ZDB-GENE-071120-2 traf2a GENE
Xenbase:XB-GENE-493460 traf2 GENE
HGNC:14300 CSRNP1 GENE
UBERON:0000002 uterine cervix ANAT
FlyBase:FBgn0043362 bchs GENE
NCBIGene:100566554 wdfy3 GENE
ZFIN:ZDB-GENE-040426-1487 rad23b GENE
UBERON:0002107 liver ANAT
MGI:106054 Psmc1 GENE
MP:0003203 increased neuron apoptosis DISO
FlyBase:FBgn0002525 Lam GENE
FBbt:00004954PHENOTYPE Drosophila spermatozoon phenotype DISO
NCBIGene:280795 FOS GENE
FlyBase:FBgn0028550 Atf3 GENE
FlyBase:FBgn0026777 Rad23 GENE
FlyBase:FBgn0086558 Ubi-p5E GENE
MGI:2447188 Car9 GENE
FlyBase:FBgn0033542 CG12309 GEN

NCBIGene:837150 GSK1 GENE
FlyBase:FBgn0003371 sgg GENE
Xenbase:XB-GENE-490369 krt17 GENE
ZFIN:ZDB-GENE-030131-7018 wu:fk65c09 GENE
WormBase:WBGene00002053 ifb-1 GENE
WBPhenotype:0000025 blistered DISO
MGI:95294 Egfr GENE
MP:0001239 abnormal epidermis stratum granulosum morphology DISO
HGNC:7782 NFE2L2 GENE
HGNC:7780 NFE2 GENE
MGI:2443788 Engase GENE
ZFIN:ZDB-GENE-070112-1332 engase GENE
ZFIN:ZDB-GENE-051023-7 uba52 GENE
MGI:1925544 Rps27a GENE
REACT:R-HSA-432040 Vasopressin regulates renal water homeostasis via Aquaporins PHYS
HP:0002171 Gliosis DISO
ZFIN:ZDB-GENE-030131-7859 jun GENE
ZP:0001143 abnormal(ly) increased size head DISO
WormBase:WBGene00004345 rgs-2 GENE
Xenbase:XB-GENE-984104 rgs17 GENE
ZFIN:ZDB-GENE-070912-475 csrnp1a GENE
UBERON:0000922 embryo ANAT
KEGG-path:maphsa04924 Renin secretion PHYS
HP:0001880 Eosinophilia DISO
WormBase:WBGene00002053 ifb-1 GENE
WormBase:WBGene00002050 ifa-1 GENE
FlyBase:FBgn0039904 Hcf GENE
FBbt:00004476PHENOTYPE Drosophila tergite phenotype DI

HGNC:17646 NGLY1 GENE
NCBIGene:100054631 MID2 GENE
HGNC:7096 MID2 GENE
FlyBase:FBgn0010397 LamC GENE
FBbt:00001878PHENOTYPE embryonic/larval salivary gland phenotype DISO
RGD:1307730 Nfe2l3 GENE
NCBIGene:463298 NFE2L3 GENE
FlyBase:FBgn0039147 CG10694 GENE
FBbt:00004178PHENOTYPE Drosophila Johnston organ phenotype DISO
MGI:1341204 Aqp6 GENE
MGI:1329027 Gk2 GENE
SGD:S000005388 YAP7 GENE
MONARCH:APO_0000059APO_0000002 vacuolar morphology:abnormal GENO
HGNC:12613 USP15 GENE
GO:0005829 cytosol PHYS
NCBIGene:505945 SRPK2 GENE
HGNC:11306 SRPK2 GENE
WormBase:WBGene00020567 T19D2.1 GENE
FlyBase:FBgn0003137 Ppn GENE
NCBIGene:617914 MAFF GENE
MGI:96910 Maff GENE
ZFIN:ZDB-GENE-080815-4 ca12 GENE
NCBIGene:100567887 ca12 GENE
Xenbase:XB-GENE-959045 creb3 GENE
WormBase:WBGene00002783 let-607 GENE
MONDO:0014109 NGLY1-deficiency DISO
HP:0200136 Oral-pharyngeal dysphagia DISO
:.well-known/genid/mgiseqaltkey2026 tm1Ask GENO
MP:0006423 dilated rete testis DISO
ClinVarVariant:221581 NM_018297.3(NGLY1):c.73

MGI:88059 App GENE
MP:0009403 increased variability of skeletal muscle fiber size DISO
RGD:68344 Uba52 GENE
MGI:3649356 Gm11808 GENE
NCBIGene:837324 ACA5 GENE
FlyBase:FBgn0034560 CG9235 GENE
MGI:99919 Vcp GENE
GO:0005829 cytosol PHYS
REACT:R-HSA-445717 Aquaporin-mediated transport PHYS
HP:0002904 Hyperbilirubinemia DISO
NCBIGene:825874 AT4G05260 GENE
ZFIN:ZDB-GENE-040426-1487 rad23b GENE
ZFIN:ZDB-GENE-060503-57 aqp10b GENE
NCBIGene:101749384 AQP10 GENE
MGI:96646 Jun GENE
MGI:98506 Tcf4 GENE
WormBase:WBGene00007574 C14B1.3 GENE
RGD:620418 Fbxo6 GENE
ClinVarVariant:221581 NM_018297.3(NGLY1):c.730T>C (p.Trp244Arg) VARI
HP:0000252 Microcephaly DISO
MGI:95294 Egfr GENE
HP:0040170 Abnormality of hair growth DISO
ZFIN:ZDB-GENE-030131-8730 psmc1a GENE
HGNC:9547 PSMC1 GENE
HGNC:463 AMFR GENE
HGNC:12458 UBA52 GENE
MGI:1339958 Nfe2l3 GENE
NCBIGene:510807 NFE2L3 GENE
FlyBase:FBgn0267821 da GENE
FBbt:00007039PHENOTYPE intestinal stem cell phenotype DISO
MGI:3781416 Gm3238 GENE
MGI:3779678 Gm7138 GE

In [11]:
with open('./add-connections-to-net/monarch_nodes_v{}.tsv'.format(today), 'w') as f:
    f.write(
        'id\tsemantic_groups\tpreflabel\tsynonyms\tdescription\n'
           )
    for concept in concept_dct:
        # semantic_groups
        semantic = concept_dct.get(concept).get('semantic_groups')
        # preflabel
        preflabel = concept_dct.get(concept).get('preflabel') 
        # synonyms
        synonyms = concept_dct.get(concept).get('synonyms') 
        # definition
        definition = concept_dct.get(concept).get('definition')
        f.write('{}\t{}\t{}\t{}\t{}\n'.format(concept,semantic,preflabel,synonyms,definition))
        print(concept,semantic,preflabel,synonyms,definition)

RGD:2145 GENE Aqp7 NA NA
RGD:1303263 GENE Gk2 NA NA
NCBIGene:427417 GENE CREB3 NA NA
MGI:99946 GENE Creb3 NA NA
FlyBase:FBgn0037244 GENE CG14647 NA NA
CL:0000023 ANAT oocyte NA NA
Xenbase:XB-GENE-990196 GENE capn1 NA NA
MGI:88263 GENE Capn1 NA NA
MGI:1309991 GENE Krt33b NA NA
RGD:1359411 GENE Krt31 NA NA
MGI:87883 GENE Acp5 NA NA
MP:0001541 DISO abnormal osteoclast physiology NA NA
KEGG-path:maphsa04976 PHYS Bile secretion NA NA
HP:0004305 DISO Involuntary movements NA NA
MGI:5011587 GENE Gm19402 NA NA
RGD:1583076 GENE LOC687631 NA NA
RGD:3090 GENE Mip NA NA
RGD:628763 GENE Aqp11 NA NA
RGD:1309121 GENE Fbxw11 NA NA
RGD:70982 GENE Gsk3b NA NA
HGNC:14078 GENE BACH2 NA NA
GO:0000980 PHYS RNA polymerase II distal enhancer sequence-specific DNA binding NA NA
FlyBase:FBgn0037788 GENE CG3940 NA NA
FBcv:0000709 DISO cell number defective NA NA
ZFIN:ZDB-GENE-060526-131 GENE rusc2 NA NA
WormBase:WBGene00006753 GENE unc-14 NA NA
NCBIGene:100055579 GENE CA9 NA NA
FlyBase:FBgn0034554 GENE CG15227 N

HP:0000689 DISO Dental malocclusion NA NA
WormBase:WBGene00002054 GENE ifb-2 NA NA
NCBIGene:100017764 GENE LMNA NA NA
HP:0001324 DISO Muscle weakness NA NA
FlyBase:FBgn0031488 GENE CG17265 NA NA
HGNC:24926 GENE CCDC85B NA NA
ZFIN:ZDB-GENE-050913-78 GENE zgc:114081 NA NA
ZFIN:ZDB-GENE-090312-52 GENE si:rp71-1k13.6 NA NA
NCBIGene:100055128 GENE KEAP1 NA NA
ZFIN:ZDB-GENE-060130-56 GENE ccdc85b NA NA
NCBIGene:100525383 GENE CCDC85B NA NA
HGNC:9547 GENE PSMC1 NA NA
NCBIGene:453097 GENE PSMC1 NA NA
ENSEMBL:ENSRNOG00000046782 GENE ENSEMBL:ENSRNOG00000046782 NA NA
GO:0030950 PHYS establishment or maintenance of actin cytoskeleton polarity NA NA
MP:0005397 DISO hematopoietic system phenotype NA NA
KEGG-path:maphsa04141 PHYS Protein processing in endoplasmic reticulum NA NA
HP:0004325 DISO Decreased body weight NA NA
MGI:1858308 GENE Tnk2 NA NA
GO:0016020 PHYS membrane NA NA
HGNC:17378 GENE NAGPA NA NA
UBERON:0002369 ANAT adrenal gland NA NA
ZFIN:ZDB-GENE-031222-4 GENE fosab NA NA
UBERON:0002107

HP:0010719 DISO Abnormality of hair texture NA NA
NCBIGene:464364 GENE DERL1 NA NA
MGI:1915069 GENE Derl1 NA NA
WormBase:WBGene00008095 GENE C44H4.6 NA NA
NCBIGene:831316 GENE SK13 NA NA
NCBIGene:100015975 GENE IKZF3 NA NA
ZFIN:ZDB-GENE-040801-41 GENE mipa NA NA
Xenbase:XB-GENE-479726 GENE aqp5 NA NA
HGNC:620 GENE APP NA NA
MP:0002999 DISO abnormal bone healing NA NA
NCBIGene:100029862 GENE UBXN2B NA NA
UBERON:0000467 ANAT anatomical system NA NA
NCBIGene:397027 GENE CAPN1 NA NA
NCBIGene:827847 GENE ACA6 NA NA
FlyBase:FBgn0025592 GENE Gk1 NA NA
MONARCH:APO_0000149APO_0000004 GENO protein/peptide accumulation:increased NA NA
ZFIN:ZDB-GENE-051023-7 GENE uba52 NA NA
GO:0045893 PHYS positive regulation of transcription, DNA-templated NA NA
MGI:106594 GENE Gk NA NA
UBERON:0000956 ANAT cerebral cortex NA NA
NCBIGene:747490 GENE VCP NA NA
NCBIGene:395614 GENE IKZF3 NA NA
RGD:620745 GENE Ubqln1 NA NA
NCBIGene:469799 GENE FBXO6 NA NA
MGI:3042273 GENE Nsfl1c NA NA
ZFIN:ZDB-GENE-030131-7764 GENE 

MP:0012099 DISO decreased spongiotrophoblast size NA NA
MP:0008428 DISO abnormal spatial working memory NA NA
GO:0071472 PHYS cellular response to salt stress NA NA
NCBIGene:698083 GENE IKZF3 NA NA
NCBIGene:100553155 GENE lmna NA NA
GO:0015670 PHYS carbon dioxide transport NA NA
NCBIGene:700466 GENE TMEM25 NA NA
HP:0001927 DISO Acanthocytosis NA NA
MONARCH:APO_0000095APO_0000005 GENO chemical compound accumulation:absent NA NA
NCBIGene:100060210 GENE UBXN1 NA NA
NCBIGene:538702 GENE LOC538702 NA NA
HP:0000980 DISO Pallor NA NA
MGI:2144023 GENE Fbxw11 NA NA
NCBIGene:100069972 GENE FBXW11 NA NA
HP:0001744 DISO Splenomegaly NA NA
WBPhenotype:0002059 DISO pore forming toxin hypersensitive NA NA
MP:0004882 DISO enlarged lung NA NA
WormBase:WBGene00017164 GENE eng-1 NA NA
MGI:1351598 GENE Nagpa NA NA
HGNC:21205 GENE LINGO1 NA NA
MGI:2174931 GENE Aqp1<tm1Ask>/Aqp1<tm1Ask> [involves: C57BL/6J] NA NA
WBPhenotype:0001969 DISO germ cell compartment morphology variant NA NA
NCBIGene:746761 GENE GK

UBERON:0000167 ANAT oral cavity NA NA
WBPhenotype:0000062 DISO lethal NA NA
NCBIGene:100057642 GENE EFEMP2 NA NA
HGNC:14237 GENE GUCD1 NA NA
UBERON:0001304 ANAT germinal epithelium of ovary NA NA
NCBIGene:100559046 GENE ubqln1 NA NA
MONARCH:APO_0000240APO_0000004 GENO mitophagy:increased NA NA
NCBIGene:416181 GENE FBXW11 NA NA
MP:0000733 DISO abnormal muscle development NA NA
NCBIGene:706173 GENE LOC706173 NA NA
NCBIGene:100152701 GENE MDFI NA NA
NCBIGene:100153716 GENE UBXN2B NA NA
NCBIGene:416677 GENE NRF1 NA NA
MGI:2152337 GENE 1110038F14Rik NA NA
FBbt:00005893PHENOTYPE DISO embryonic/larval peripheral nervous system phenotype NA NA
GO:0048786PHENOTYPE PHYS presynaptic active zone phenotype NA NA
Xenbase:XB-GENE-484060 GENE aqp7 NA NA
HGNC:24082 GENE C3orf35 NA NA
MP:0011091 DISO prenatal lethality, complete penetrance NA NA
WBPhenotype:0000038 DISO exploded through vulva NA NA
MGI:2147607 GENE Ccdc85b NA NA
HP:0007703 DISO Abnormality of retinal pigmentation NA NA
UBERON:0002436 AN

...

FBbt:00000424PHENOTYPE DISO Drosophila embryonic/larval posterior spiracle phenotype NA NA
FBbt:00001694PHENOTYPE DISO Drosophila embryonic/larval oenocyte phenotype NA NA
GO:0020005 PHYS symbiont-containing vacuole membrane NA NA
GO:0060070PHENOTYPE PHYS canonical Wnt signaling pathway phenotype NA NA
MP:0005168 DISO abnormal female meiosis NA NA
MP:0001280 DISO loss of vibrissae NA NA
AQTLTrait:1330 DISO Channel fat weight NA NA
WBPhenotype:0002187 DISO ectopic body wall muscle NA NA
MP:0003051 DISO curly tail NA NA
NCBIGene:695404 GENE NFE2L1 NA NA
MP:0009653 DISO abnormal palate development NA NA
HP:0003330 DISO Abnormal bone structure NA NA
MP:0003843 DISO abnormal sagittal suture morphology NA NA
ZP:0000050 DISO abnormal(ly) decreased size optic tectum NA NA
NCBIGene:707352 GENE NAGPA NA NA
MP:0020161 DISO increased vascular endothelial cell proliferation NA NA
ZP:0000959 DISO abnormal(ly) mislocalised liver NA NA
WBPhenotype:0001236 DISO transgene expression increased NA NA
MP:0

NCBIGene:823619 GENE AT3G44850 NA NA
MP:0013772 DISO increased effector memory T-helper cell number NA NA
FBbt:00003138PHENOTYPE DISO Drosophila adult midgut phenotype NA NA
FBbt:00004340PHENOTYPE DISO wing hair phenotype NA NA
AQTLTrait:1050 DISO Body weight (400 days) NA NA
MP:0005566 DISO decreased blood urea nitrogen level NA NA
MP:0001622 DISO abnormal vasculogenesis NA NA
ZP:0000004 DISO abnormal(ly) disrupted determination of left/right asymmetry in lateral mesoderm NA NA
FBbt:00001920PHENOTYPE DISO embryonic/larval brain phenotype NA NA
MP:0000350 DISO abnormal cell proliferation NA NA
HP:0010976 DISO B lymphocytopenia NA NA
HP:0001679 DISO Abnormal aortic morphology NA NA
FBbt:00004477PHENOTYPE DISO Drosophila sternite phenotype NA NA
HP:0000029 DISO Testicular atrophy NA NA
FBbt:00001911PHENOTYPE DISO embryonic/larval nervous system phenotype NA NA
MP:0009375 DISO thin zona pellucida NA NA
MP:0003442 DISO decreased circulating glycerol level NA NA
MP:0003841 DISO abnormal lam

ZP:0003096 DISO abnormal(ly) decreased size esophagus muscle NA NA
Coriell:GM25344 GENO NIGMS-GM25344 NA NA
FBcv:0000408 DISO stress response defective NA NA
FBbt:00000755PHENOTYPE DISO abdominal 3 lateral longitudinal muscle 1 phenotype NA NA
MP:0008918 DISO microgliosis NA NA
FBbt:00005807PHENOTYPE DISO Drosophila dorsal pouch phenotype NA NA
ZP:0012156 DISO abnormal(ly) morphology diencephalon cell junction NA NA
MP:0001302 DISO eyelids open at birth NA NA
MP:0001195 DISO flaky skin NA NA
WBPhenotype:0001139 DISO nuclear envelope assembly variant early emb NA NA
FBbt:00000197PHENOTYPE DISO posterior spiracle primordium phenotype NA NA
FBbt:00000407PHENOTYPE DISO embryonic/larval anterior spiracle phenotype NA NA
FBbt:00000612PHENOTYPE DISO Drosophila A1-7 dorsal oblique muscle 4 phenotype NA NA
ZFIN:ZDB-GENE-070815-2 GENE adamtsl4 NA NA
MP:0000378 DISO absent hair follicles NA NA
MP:0010872 DISO increased trabecular bone mass NA NA
MP:0009762 DISO abnormal mitotic spindle assembly c

FBbt:00004762PHENOTYPE DISO wing vein L4 phenotype NA NA
AQTLTrait:1302 DISO Milk myristoleic acid percentage NA NA
FBcv:0000379 DISO enhancer of variegation NA NA
GO:0015079 PHYS potassium ion transmembrane transporter activity NA NA
MP:0001488 DISO increased startle reflex NA NA
ZP:0002441 DISO abnormal(ly) increased rate neuron apoptotic process NA NA
MP:0020408 DISO altered susceptibility to induced thrombosis NA NA
GO:0015696PHENOTYPE PHYS ammonium transport phenotype NA NA
WBPhenotype:0001951 DISO pachytene region organization variant NA NA
WBPhenotype:0002078 DISO histone methylation variant NA NA
MP:0011078 DISO increased macrophage cytokine production NA NA
FBbt:00001433PHENOTYPE DISO Drosophila embryonic ganglion mother cell phenotype NA NA
GO:0042472PHENOTYPE PHYS inner ear morphogenesis phenotype NA NA
MP:0009395 DISO increased nucleated erythrocyte cell number NA NA
ZP:0010878 DISO abnormal(ly) has extra parts of type otic vesicle towards hair cell NA NA
FBbt:00000328PHENO

FBbt:00002908PHENOTYPE DISO Drosophila abdominal 4 ventral monoscolopidial chordotonal organ vch1 phenotype NA NA
MP:0008535 DISO enlarged lateral ventricles NA NA
MP:0005493 DISO stomach epithelial hyperplasia NA NA
MP:0001932 DISO abnormal spermiogenesis NA NA
ZP:0000160 DISO abnormal(ly) dorsalized whole organism NA NA
MONARCH:APO_0000149APO_0000249 GENO protein/peptide accumulation:delayed NA NA
FBbt:00000463PHENOTYPE DISO embryonic myoblast phenotype NA NA
MP:0005431 DISO decreased oocyte number NA NA
MP:0012752 DISO abnormal cardiac neural crest cell migration NA NA
MP:0005091 DISO increased double-positive T cell number NA NA
FBbt:00004745PHENOTYPE DISO Drosophila axillary pouch phenotype NA NA
MP:0002268 DISO abnormal terminal bronchiole morphology NA NA
ClinVarVariant:474218 VARI NM_018297.3(NGLY1):c.1875C>G (p.Val625=) NA NA
MP:0001168 DISO abnormal prostate gland epithelium morphology NA NA
ClinVarVariant:488990 VARI NM_018297.3(NGLY1):c.1405C>T (p.Arg469Ter) NA NA
FBbt:0000